# Description

This notebook takes in the sim_cahce file from the benrules_v2 simulator that runs random simulations on a given number of satellites.  We will extract the satellite data from all the the run simulations and combine into a single pandas dataframe. \

First part of the notebook is dedicated to visualizing satellite position over time.

# Imports

In [1]:
# Data Processing Libraries
import numpy as np
import pandas as pd
# Randomization Libraries to Select Random Points in the simulation.
import random
# Libraries for file reading
import h5py
# Bokeh and plotting related imports
# Plotting Imports
import bokeh.io
bokeh.io.output_notebook()  # Set plot output to embed in notebook.
import bokeh.layouts
import bokeh.plotting
# Other imports for multi-plot figures.
from bokeh.io import output_file, show
from bokeh.layouts import column
from bokeh.plotting import figure
# Memory management libraries for Python
import gc
# Progress Bar Libraries
from tqdm import tqdm

Loading BokehJS ...

In [2]:
# Remove max columns and row limit on pandas
pd.options.display.max_columns = None
pd.options.display.max_rows = 50000

# Setup Plotting Functions

In [3]:
from bokeh.palettes import Turbo256 as palette
import itertools
from random import randint

def plot_2D_body_time_series(pos_x_list, pos_y_list, plot_width, plot_height, title):
    """
    Accepts lists for x and y dimensions whose elements are time series data and whose
    index represents the number of the body in the simulation.
    
    returns Bokeh figure to plot.
    """
    # Create Bokeh figure to add plots to
    f = bokeh.plotting.figure(
        title = title,
        plot_width = plot_width,
        plot_height = plot_height
    )

    # Generate line for each body.
    # Randomly select color from palette using randint
    for i in range(0,len(pos_x_list)):
        f.line(
            pos_x_list[i],
            pos_y_list[i],
            line_width = 1,
            color = palette[randint(0,255)],
            legend_label = str(i)
        )
    f.legend.location = 'top_left'
    return f

def two_dim_numpy_data_to_2D_pos_list(sat_pos_list):
    """
    Take in a list of satellite position data and split into X and Y position data lists for 
    each dimension.
    """
    pos_x_list = []
    pos_y_list = []
    # Take the 2D (X and Y) time series elements of the sat_pos_list and split into the 
    # Pos_x and Pos_y lists
    for satellite_pos in sat_pos_list:
        temp_x_time_series = satellite_pos[:,0]
        temp_y_time_series = satellite_pos[:,1]
        pos_x_list.append(temp_x_time_series)
        pos_y_list.append(temp_y_time_series)
    return pos_x_list, pos_y_list

def plot_data_conv_3D_np_pos_to_2D_pos_list(pos_np_array):
    """
    Accepts 3D position numpy array and extracts the time steps for each body from 
    the numpy array.  Adds those time series for each dimension to a list of 1D numpy arrays.
    """
    # List of bodies for each dimension whose elements are numpy arrays going back in time.  
    # Each element is a time series for that body and that body's dimension.
    pos_x_list = []
    pos_y_list = []
    # First index of the numpy array is the time step and second is the body number.  Will loop
    # over all bodies and slice out the time steps for each body.
    for current_body_index in range(0, pos_np_array.shape[1]):
        # Get slice of data to create time series of position values
        # Use .to_numpy() to convert to numpy array
        temp_x_time_series = pos_np_array[:, current_body_index, 0]
        temp_y_time_series = pos_np_array[:, current_body_index, 1]
        # Add time series to respective dimension.
        pos_x_list.append(temp_x_time_series)
        pos_y_list.append(temp_y_time_series)
    
    # TODO: Continue with this function to get the position data plotted.
    return pos_x_list, pos_y_list

# Read in HDF5 Files to Lists of Numpy Arrays

In [4]:
# Set folder to read hdf5 cache file from.
in_data_folder = "input_data/"
# Body index in the numpy arrays from the simulation that designates the satellite from 
# the planets
sat_index: int = 10
# Lists for storing the satellite data from each simulation in the cache.
acc_list = []
vel_list = []
pos_list = []
dis_list = []
mass_list = []

# Open the sim_cache, get the data groups, and extract datasets from it.
with h5py.File(in_data_folder + 'sim_cache.hdf5', 'r') as f:
    # Get all the groups and data_set keys
    group_keys = []
    for key in f.keys():
        group_keys.append(key)
    # Loop over all groups in the dataset and extract the numpy arrays
    for group_name in group_keys:
        group = f[group_name]
        # Grab the raw data from the file.
        temp_acc = group['acc'][()]
        temp_vel = group['vel'][()]
        temp_pos = group['pos'][()]
        temp_dis = group['dis'][()]
        temp_mass = group['mass'][()]
        # Extract the Satellite data only
        # Only grabbing X and Y dimensions
        temp_acc = temp_acc[:, sat_index, 0:2]
        temp_vel = temp_vel[:, sat_index, 0:2]
        temp_pos = temp_pos[:, sat_index, 0:2]
        temp_dis = temp_dis[:, sat_index, 0:2]
        temp_mass = temp_mass[sat_index, 0]
        
        acc_list.append(temp_acc)
        vel_list.append(temp_vel)
        pos_list.append(temp_pos)
        dis_list.append(temp_dis)
        mass_list.append(temp_mass)

In [5]:
pos_list[0]

array([[ 1.3840513e+11,  5.6425894e+10],
       [ 1.3857676e+11,  5.5451226e+10],
       [ 1.3873925e+11,  5.4471561e+10],
       ...,
       [ 5.3256200e+10, -6.8380451e+10],
       [ 5.1455967e+10, -6.8805820e+10],
       [ 4.9635631e+10, -6.9204312e+10]], dtype=float32)

In [6]:
pos_list[0][:,0].shape

(39999,)

In [7]:
mass_list

[1476.0, 2824.0, 2360.0, 3703.0, 1801.0, 1521.0, 614.0, 3559.0, 3512.0, 1805.0]

# Plot the path of the Specified Satellite

In [8]:
# Convert all the satellite data to a list of time series for plotting.
# Will plot all satellites on the same plot.
pos_x_list, pos_y_list = two_dim_numpy_data_to_2D_pos_list(pos_list)

In [9]:
# Plot the converted data.
fig = plot_2D_body_time_series(
    pos_x_list = pos_x_list,
    pos_y_list = pos_y_list,
    plot_width = 800,
    plot_height = 800,
    title = "Paths of All Satellites for All Simulations"
)

bokeh.plotting.show(fig)

# Plot the Whole Universe with its Associated Satellite

Get the position data for the specified satellite and its universe and plot it.

In [10]:
# Set folder to read hdf5 cache file from.
in_data_folder = "input_data/"
# Index for the simulation to grab
sim_index: int = 0
# Lists for storing the satellite data from each simulation in the cache.
raw_pos_np = None

# Open the sim_cache, get the data groups, and extract datasets from it.
with h5py.File(in_data_folder + 'sim_cache.hdf5', 'r') as f:
    # Get data group for the specified index
    group_key = 'sim_' + str(sim_index)
    # Grab the position data for all bodies in that group.
    group = f[group_key]
    # Grab the raw data from the file.
    raw_pos_np = group['pos'][()]
# Convert to list of time series for plotting.  
pos_x_list, pos_y_list = plot_data_conv_3D_np_pos_to_2D_pos_list(raw_pos_np)
del raw_pos_np
# Plot the converted data.
fig = plot_2D_body_time_series(
    pos_x_list = pos_x_list,
    pos_y_list = pos_y_list,
    plot_width = 800,
    plot_height = 800,
    title = "Path of sat {} with Universe".format(sim_index)
)

bokeh.plotting.show(fig)

# Convert Acceleration, Velocity, Displacement, and Position Numpy Arrays to Pandas Dataframes

In [11]:
# Set the number of "shotgun" future time steps to predict.
num_ts_to_predict = 20

### Converting Acceleration to Pandas DataFrame

In [12]:
acc_list[0]

array([[-0.00334952, -0.00389397],
       [-0.00497867, -0.00262359],
       [-0.00531293, -0.00236606],
       ...,
       [-0.0108596 ,  0.01393398],
       [-0.01077147,  0.01439314],
       [-0.01066916,  0.01486455]], dtype=float32)

In [13]:
# Stack all the satellites as bodies into a single numpy array.
stacked_raw_acc = np.stack(acc_list, axis=1)
stacked_raw_acc.shape

(39999, 10, 2)

In [14]:
# Construct the acceleration dataframe from the raw simulator velocity output data.
# Get the size of each dimension in numpy array.
# m-> the number of time steps in the simulation.
# n-> the number of bodies in the simulation.
# r-> number of dimensions in the vector holding the acceleration, displacement, etc.
acc_m,acc_n,acc_r = stacked_raw_acc.shape
# Stack the XY or XYZ arrays of each body into columns, removing a dimension.
# np.column_stack() -> takes a sequence of 1D arrays and stacks them as columns in a 2D matrix.
# np.arange() provides evenly spaced values that repeat n times.  The new index.
# Had to add 1 to arange to go from 1 to 79 instead of 0.
acc_arr = np.column_stack(
    (np.repeat(np.arange(1, acc_m+1, 1),acc_n), 
     np.tile(np.arange(0,acc_n,1),acc_m), 
     stacked_raw_acc[:,:,0:2].reshape(acc_m*acc_n,-1))
)

# Create dataframe from stacked column array.
acc_df = pd.DataFrame(acc_arr)
# Delete intermediate numpy arrays and original data from memory.
del acc_arr
gc.collect()
# Use df.groupby() to group by time step or planent and create MultiIndex for easy data referencing.
acc_df = acc_df.groupby([0,1]).mean()
acc_df.index.names = ['time_step', 'body']
acc_df.columns = ['acc_x', 'acc_y']
# Swapping to time_step then body to keep compatibility with existing code.
#acc_df = acc_df.swaplevel('time_step', 'body').sort_index(level=0)
#acc_df.head(15)
idx = pd.IndexSlice
acc_df.loc[idx[1, :], :]

acc_x     acc_y
time_step body                    
1.0       0.0  -0.003350 -0.003894
          1.0   0.001788 -0.004374
          2.0  -0.001583 -0.004751
          3.0  -0.004363 -0.003255
          4.0  -0.000145 -0.003863
          5.0  -0.002421 -0.003808
          6.0  -0.002636 -0.003789
          7.0  -0.002112 -0.004053
          8.0  -0.004331 -0.003563
          9.0  -0.001876 -0.004625

In [15]:
# Drop the time steps that could not be used for calculating displacecment.
# Create list of time steps to drop.
beg_drop_index = max(acc_df.index.levels[0]) - num_ts_to_predict + 1
end_drop_index = max(acc_df.index.levels[0]) + 1
drop_list = list(range(int(beg_drop_index), int(end_drop_index)))
# Drop the time steps from the displacement dataframe.
acc_df.drop(drop_list, level=0, inplace=True)
# Ouput the new dataframe
acc_df.head(10)

acc_x     acc_y
time_step body                    
1.0       0.0  -0.003350 -0.003894
          1.0   0.001788 -0.004374
          2.0  -0.001583 -0.004751
          3.0  -0.004363 -0.003255
          4.0  -0.000145 -0.003863
          5.0  -0.002421 -0.003808
          6.0  -0.002636 -0.003789
          7.0  -0.002112 -0.004053
          8.0  -0.004331 -0.003563
          9.0  -0.001876 -0.004625

In [16]:
acc_df.shape

(399790, 2)

### Converting Velocity to Pandas DataFrame

Dataframes are really slow.  We will need to calculate the future velocities for num_ts_to_predict so that we can shotgun predict multiple time steps at the same time.  We want to do this with numpy arrays before converting to a pandas dataframe for easy grouping and indexing. \
Will first need to go through and calculate the future time steps to shotgun-predict.

In [17]:
vel_list[0]

array([[  4071.5686, -22489.678 ],
       [  3879.7585, -22621.006 ],
       [  3656.0425, -22727.703 ],
       ...,
       [-41405.836 , -10162.394 ],
       [-41873.086 ,  -9550.406 ],
       [-42336.227 ,  -8918.316 ]], dtype=float32)

In [18]:
# Stack all the satellites as bodies into a single numpy array.
stacked_raw_vel = np.stack(vel_list, axis=1)
stacked_raw_vel.shape

(39999, 10, 2)

In [19]:
# Create a numpy array with the same first 2 dimensions of the input data (time steps and num bodies)
# the number of columns will be the same as the number of time steps
# being predicted multiplied by the dimensions (2) (X and Y)
vel_pred_cache = np.full(
    (stacked_raw_vel.shape[0], stacked_raw_vel.shape[1], num_ts_to_predict*2),
    np.nan,
    dtype=np.float32
)
# Loop over all time steps in the numpy array.
# Grab groups of bodies from future time steps
for curr_time_step in tqdm(range(0, stacked_raw_vel.shape[0])):
    # Loop over the number of time steps in the future to be grabbing
    # velocities from.
    # Don't do last time steps for displacement dataframe.  Can only look so many
    # time steps into the future before running out of data.
    if curr_time_step < (stacked_raw_vel.shape[0] - num_ts_to_predict):
        for num_ts_in_future in range(1, num_ts_to_predict + 1):
            vel_pred_cache[int(curr_time_step), :, int(2*num_ts_in_future-2):int(2*num_ts_in_future)] = \
            stacked_raw_vel[int(curr_time_step + num_ts_in_future), :, 0:2]
            
# Concatenate the cached numpy array to the original velocity dataset
stacked_raw_vel = np.concatenate((stacked_raw_vel[:,:,0:2], vel_pred_cache), axis=2)
# Delete the cache.
del vel_pred_cache
gc.collect()
#Display first portion of the dataframe
pd.DataFrame(stacked_raw_vel[0])

100%|██████████| 39999/39999 [00:01<00:00, 28762.47it/s]


0             1            2             3            4  \
0  4071.568604 -22489.677734  3879.758545 -22621.005859  3656.042480   
1  6419.551758 -26621.166016  6345.174805 -26761.347656  6165.222656   
2  5501.831055 -24396.433594  5349.671875 -24545.843750  5140.319336   
3  2148.510742 -19890.517578  1934.510498 -20008.482422  1703.021362   
4  5535.345703 -26215.746094  5415.373047 -26345.796875  5217.470215   
5  4247.180664 -24364.169922  4075.638672 -24493.599609  3858.778564   
6  4102.775879 -24070.669922  3926.463379 -24199.699219  3707.915527   
7  4675.142090 -24449.644531  4510.599121 -24584.228516  4296.371582   
8  3662.585938 -19540.166016  3449.612061 -19664.544922  3218.943115   
9  5330.547852 -24173.341797  5171.720215 -24320.093750  4959.904785   

              5            6             7            8             9  \
0 -22727.703125  3423.163574 -22827.263672  3185.787598 -22923.167969   
1 -26869.894531  5955.413086 -26969.478516  5732.338379 -27064.494141   
2 -24658.281250  4914.957031 -24760.298828  4682.282227 -24857.218750   
3 -20111.208984  1466.101196 -20209.361328  1226.169922 -20305.060547   
4 -26451.404297  4997.791992 -26549.761719  4768.313965 -26644.257812   
5 -24599.482422  3629.138184 -24698.419922  3393.454102 -24793.710938   
6 -24305.501953  3477.416260 -24404.443359  3241.215332 -24499.796875   
7 -24691.775391  4068.204102 -24791.468750  3833.536377 -24887.125000   
8 -19769.205078  2982.921875 -19868.099609  2744.046875 -19964.007812   
9 -24431.673828  4733.245117 -24533.316406  4499.758301 -24630.070312   

            10            11           12            13           14  \
0  2945.481445 -23016.585938  2702.914795 -23107.994141  2458.417725   
1  5501.805664 -27156.347656  5266.393066 -27245.638672  5027.416016   
2  4445.263672 -24950.814453  4205.198730 -25041.833984  3962.738770   
3   984.022949 -20399.013672   739.988831 -20491.515625   494.219177   
4  4533.159180 -26735.990234  4294.134277 -26825.427734  4052.158936   
5  3154.003906 -24886.447266  2911.768555 -24977.095703  2667.238525   
6  3001.423096 -24592.638672  2758.947510 -24683.427734  2514.239014   
7  3594.894043 -24980.015625  3353.368896 -25070.683594  3109.508789   
8  2503.147461 -20057.857422  2260.567139 -20150.037109  2016.469482   
9  4262.174805 -24723.607422  4021.682617 -24814.654297  3778.878418   

             15           16            17           18            19  \
0 -23197.640625  2212.165527 -23285.652344  1964.258301 -23372.097656   
1 -27332.671875  4785.624023 -27417.587891  4541.472168 -27500.474609   
2 -25130.650391  3718.244385 -25217.464844  3471.935059 -25302.394531   
3 -20582.701172   246.787247 -20672.654297    -2.273598 -20761.406250   
4 -26912.791016  3807.744629 -26998.199219  3561.203369 -27081.714844   
5 -25065.873047  2420.683105 -25152.898438  2172.260498 -25238.236328   
6 -24772.376953  2267.545654 -24859.615234  2019.011475 -24945.193359   
7 -25159.386719  2863.614502 -25246.257812  2615.864014 -25331.378906   
8 -20240.740234  1770.935547 -20330.072266  1524.005615 -20418.091797   
9 -24903.552734  3534.093018 -24990.496094  3287.525635 -25075.591797   

            20            21           22            23           24  \
0  1714.756470 -23457.017578  1463.693481 -23540.435547  1211.088501   
1  4295.256348 -27581.380859  4047.171387 -27660.332031  3797.364746   
2  3223.945312 -25385.500000  2974.365967 -25466.828125  2723.257080   
3  -252.951767 -20848.984375  -505.248810 -20935.410156  -759.174622   
4  3312.734619 -27163.367188  3062.469971 -27243.171875  2810.504883   
5  1922.068848 -25321.919922  1670.166504 -25403.964844  1416.594604   
6  1768.723999 -25029.146484  1516.737549 -25111.490234  1263.086792   
7  2366.372314 -25414.791016  2115.207275 -25496.515625  1862.416992   
8  1275.698242 -20504.833984  1026.017090 -20590.318359   774.958374   
9  3039.296631 -25158.912109  2789.488525 -25240.476562  2538.154541   

             25           

In [20]:
# Construct the velocity dataframe from the raw simulator velocity output data.
# Get the size of each dimension in numpy array.
# m-> the number of time steps in the simulation.
# n-> the number of bodies in the simulation.
# r-> number of dimensions in the vector holding the acceleration, displacement, etc.
vel_m,vel_n,vel_r = stacked_raw_vel.shape
# Stack the XY or XYZ arrays of each body into columns, removing a dimension.
# np.column_stack() -> takes a sequence of 1D arrays and stacks them as columns in a 2D matrix.
# np.arange() provides evenly spaced values that repeat n times.  The new index.
# Had to add 1 to arange to go from 1 to 79 instead of 0.
vel_arr = np.column_stack(
    (np.repeat(np.arange(1, vel_m+1, 1),vel_n), 
     np.tile(np.arange(0,vel_n,1),vel_m), 
    stacked_raw_vel.reshape(vel_m*vel_n,-1))
)
# Create dataframe from stacked column array.
vel_df = pd.DataFrame(vel_arr)
# Delete intermediate numpy arrays and original data from memory.
del vel_arr
gc.collect()
# Use df.groupby() to group by time step or planent and create MultiIndex for easy data referencing.
vel_df = vel_df.groupby([0,1]).mean()
vel_df.index.names = ['time_step', 'body']
# Drop the time steps that could not be used for getting future data.
# Create list of time steps to drop.
beg_drop_index = max(vel_df.index.levels[0]) - num_ts_to_predict + 1
end_drop_index = max(vel_df.index.levels[0]) + 1
drop_list = list(range(int(beg_drop_index), int(end_drop_index)))
vel_df.drop(drop_list, level=0, inplace=True)
# Create list of columns 
cols = ['vel_x', 'vel_y']
for i in range(1, num_ts_to_predict+1):
    cols.append('vel_x_' + str(i))
    cols.append('vel_y_' + str(i))
vel_df.columns = cols
# View final velocity dataframe with future time steps.
idx = pd.IndexSlice
vel_df.loc[idx[0:2,:], :]

vel_x         vel_y      vel_x_1       vel_y_1  \
time_step body                                                         
1.0       0.0   4071.568604 -22489.677734  3879.758545 -22621.005859   
          1.0   6419.551758 -26621.166016  6345.174805 -26761.347656   
          2.0   5501.831055 -24396.433594  5349.671875 -24545.843750   
          3.0   2148.510742 -19890.517578  1934.510498 -20008.482422   
          4.0   5535.345703 -26215.746094  5415.373047 -26345.796875   
          5.0   4247.180664 -24364.169922  4075.638672 -24493.599609   
          6.0   4102.775879 -24070.669922  3926.463379 -24199.699219   
          7.0   4675.142090 -24449.644531  4510.599121 -24584.228516   
          8.0   3662.585938 -19540.166016  3449.612061 -19664.544922   
          9.0   5330.547852 -24173.341797  5171.720215 -24320.093750   
2.0       0.0   3879.758545 -22621.005859  3656.042480 -22727.703125   
          1.0   6345.174805 -26761.347656  6165.222656 -26869.894531   
          2.0   5349.671875 -24545.843750  5140.319336 -24658.281250   
          3.0   1934.510498 -20008.482422  1703.021362 -20111.208984   
          4.0   5415.373047 -26345.796875  5217.470215 -26451.404297   
          5.0   4075.638672 -24493.599609  3858.778564 -24599.482422   
          6.0   3926.463379 -24199.699219  3707.915527 -24305.501953   
          7.0   4510.599121 -24584.228516  4296.371582 -24691.775391   
          8.0   3449.612061 -19664.544922  3218.943115 -19769.205078   
          9.0   5171.720215 -24320.093750  4959.904785 -24431.673828   

                    vel_x_2       vel_y_2      vel_x_3       vel_y_3  \
time_step body                                                         
1.0       0.0   3656.042480 -22727.703125  3423.163574 -22827.263672   
          1.0   6165.222656 -26869.894531  5955.413086 -26969.478516   
          2.0   5140.319336 -24658.281250  4914.957031 -24760.298828   
          3.0   1703.021362 -20111.208984  1466.101196 -20209.361328   
          4.0   5217.470215 -26451.404297  4997.791992 -26549.761719   
          5.0   3858.778564 -24599.482422  3629.138184 -24698.419922   
          6.0   3707.915527 -24305.501953  3477.416260 -24404.443359   
          7.0   4296.371582 -24691.775391  4068.204102 -24791.468750   
          8.0   3218.943115 -19769.205078  2982.921875 -19868.099609   
          9.0   4959.904785 -24431.673828  4733.245117 -24533.316406   
2.0       0.0   3423.163574 -22827.263672  3185.787598 -22923.167969   
          1.0   5955.413086 -26969.478516  5732.338379 -27064.494141   
          2.0   4914.957031 -24760.298828  4682.282227 -24857.218750   
          3.0   1466.101196 -20209.361328  1226.169922 -20305.060547   
          4.0   4997.791992 -26549.761719  4768.313965 -26644.257812   
          5.0   3629.138184 -24698.419922  3393.454102 -24793.710938   
          6.0   3477.416260 -24404.443359  3241.215332 -24499.796875   
          7.0   4068.204102 -24791.468750  3833.536377 -24887.125000   
          8.0   2982.921875 -19868.099609  2744.046875 -19964.007812   
          9.0   4733.245117 -24533.316406  4499.758301 -24630.070312   

                    vel_x_4       vel_y_4      vel_x_5       vel_y_5  \
time_step body                                                         
1.0       0.0   3185.787598 -22923.167969  2945.481445 -23016.585938   
          1.0   5732.338379 -27064.494141  5501.805664 -27156.347656   
          2.0   4682.282227 -24857.218750  4445.263672 -24950.814453   
          3.0   1226.169922 -20305.060547   984.022949 -20399.013672   
          4.0   4768.313965 -26644.257812  4533.159180 -26735.990234   
          5.0   3393.454102 -24793.710938  3154.003906 -24886.447266   
          6.0   3241.215332 -24499.796875  3001.423096 -24592.638672   
          7.0   3833.536377 -24887.125000  3594.894043 -24980.015625   
          8.0   2744.046875 -19964.007812  2503.147461 -20057.857422   
          9.0   4499.758301 -24630.070312  4262.174805 -2472

In [21]:
vel_df.shape

(399790, 42)

### Converting Displacement to Pandas DataFrame

In [22]:
# Stack all the satellites as bodies into a single numpy array.
stacked_raw_dis = np.stack(dis_list, axis=1)
stacked_raw_dis.shape

(39999, 10, 2)

In [23]:
# Create a numpy array with the same first 2 dimensions of the input data (time steps and num bodies)
# the number of columns will be the same as the number of time steps
# being predicted multiplied by the dimensions (2) (X and Y)
dis_pred_cache = np.full(
    (stacked_raw_dis.shape[0], stacked_raw_dis.shape[1], num_ts_to_predict*2),
    np.nan,
    dtype=np.float32
)
# Loop over all time steps in the numpy array.
# Grab groups of bodies from future time steps
for curr_time_step in tqdm(range(0, stacked_raw_dis.shape[0])):
    # Loop over the number of time steps in the future to be grabbing
    # velocities from.
    # Don't do last time steps for displacement dataframe.  Can only look so many
    # time steps into the future before running out of data.
    if curr_time_step < (stacked_raw_dis.shape[0] - num_ts_to_predict):
        for num_ts_in_future in range(1, num_ts_to_predict + 1):
            dis_pred_cache[int(curr_time_step), :, int(2*num_ts_in_future-2):int(2*num_ts_in_future)] = \
            stacked_raw_dis[int(curr_time_step + num_ts_in_future), :, 0:2]
            
# Concatenate the cached numpy array to the original displacement dataset
stacked_raw_dis = np.concatenate((stacked_raw_dis[:,:,0:2], dis_pred_cache), axis=2)
# Delete the cache.
del dis_pred_cache
gc.collect()
#Display first portion of the dataframe
pd.DataFrame(stacked_raw_dis[0])

100%|██████████| 39999/39999 [00:01<00:00, 29894.61it/s]


0           1           2           3            4           5  \
0  2931529.50 -16192568.0  2793426.25 -16287124.0  2632350.500 -16363946.0   
1  4622077.50 -19167240.0  4568526.00 -19268170.0  4438960.500 -19346324.0   
2  3961318.25 -17565432.0  3851763.75 -17673008.0  3701030.000 -17753962.0   
3  1546927.75 -14321173.0  1392847.50 -14406107.0  1226175.375 -14480070.0   
4  3985449.00 -18875338.0  3899068.50 -18968974.0  3756578.500 -19045012.0   
5  3057970.00 -17542202.0  2934459.75 -17635392.0  2778320.500 -17711628.0   
6  2953998.75 -17330882.0  2827053.75 -17423784.0  2669699.250 -17499962.0   
7  3366102.25 -17603744.0  3247631.25 -17700644.0  3093387.500 -17778078.0   
8  2637062.00 -14068920.0  2483720.75 -14158472.0  2317639.000 -14233828.0   
9  3837994.50 -17404806.0  3723638.50 -17510468.0  3571131.500 -17590806.0   

             6           7            8           9           10          11  \
0  2464677.750 -16435630.0  2293767.000 -16504681.0  2120746.750 -16571942.0   
1  4287897.500 -19418024.0  4127283.750 -19486436.0  3961300.000 -19552570.0   
2  3538769.000 -17827416.0  3371243.250 -17897198.0  3200589.750 -17964586.0   
3  1055592.875 -14550740.0   882842.375 -14619644.0   708496.500 -14687290.0   
4  3598410.250 -19115828.0  3433186.000 -19183866.0  3263874.500 -19249912.0   
5  2612979.500 -17782862.0  2443287.000 -17851472.0  2270882.750 -17918242.0   
6  2503739.750 -17571200.0  2333675.000 -17639854.0  2161024.750 -17706700.0   
7  2929107.000 -17849858.0  2760146.250 -17918730.0  2588323.750 -17985612.0   
8  2147703.750 -14305032.0  1975713.750 -14374086.0  1802266.125 -14441657.0   
9  3407936.500 -17663988.0  3239826.000 -17733650.0  3068765.750 -17800998.0   

             12          13            14          15            16  \
0  1.946099e+06 -16637756.0  1.770061e+06 -16702301.0  1.592759e+06   
1  3.791803e+06 -19616860.0  3.619740e+06 -19679524.0  3.445649e+06   
2  3.027743e+06 -18030120.0  2.853172e+06 -18094068.0  2.677136e+06   
3  5.327919e+05 -14753891.0  3.558378e+05 -14819545.0  1.776868e+05   
4  3.091777e+06 -19314308.0  2.917554e+06 -19377210.0  2.741576e+06   
5  2.096473e+06 -17983508.0  1.920412e+06 -18047428.0  1.742892e+06   
6  1.986442e+06 -17772068.0  1.810252e+06 -17836112.0  1.632633e+06   
7  2.414426e+06 -18050892.0  2.238846e+06 -18114758.0  2.061802e+06   
8  1.627608e+06 -14508027.0  1.451858e+06 -14573333.0  1.275074e+06   
9  2.895612e+06 -17866552.0  2.720792e+06 -17930558.0  2.544547e+06   

           17            18          19            20          21  \
0 -16765670.0  1.414266e+06 -16827910.0  1.234625e+06 -16889052.0   
1 -19740664.0  3.269860e+06 -19800342.0  3.092584e+06 -19858594.0   
2 -18156574.0  2.499793e+06 -18217724.0  2.321240e+06 -18277560.0   
3 -14884311.0 -1.636991e+03 -14948212.0 -1.821253e+05 -15011269.0   
4 -19438704.0  2.564066e+06 -19498834.0  2.385169e+06 -19557624.0   
5 -18110086.0  1.564028e+06 -18171530.0  1.383890e+06 -18231782.0   
6 -17898922.0  1.453688e+06 -17960540.0  1.273481e+06 -18020986.0   
7 -18177306.0  1.883422e+06 -18238592.0  1.703788e+06 -18298650.0   
8 -14637652.0  1.097284e+06 -14701026.0  9.185028e+05 -14763480.0   
9 -17993158.0  2.367018e+06 -18054426.0  2.188294e+06 -18114416.0   

             22          23           24          25            26  \
0  1.053859e+06 -16949114.0   871983.750 -17008098.0  6.890039e+05   
1  2.913964e+06 -19915440.0  2734102.500 -19970882.0  2.553075e+06   
2  2.141544e+06 -18336116.0  1960745.125 -18393406.0  1.778876e+06   
3 -3.637792e+05 -15073495.0  -546605.750 -15134885.0 -7.306162e+05   
4  2.204978e+06 -19615084.0  2023563.500 -19671218.0  1.840971e+06   
5  1.202520e+06 -18290854.0  1019948.125 -18348752.0  8.361919e+05   
6  1.092051e+06 -18080272.0   909422.500 -18138408.0  7.256108e+05   
7  1.522949e+06 -18357492.0  1340940.250 -18415124.0  1.157784e+06   
8  7.387323e+05 -14825029.0   557970.000 -14885679.0  3.762089e+05   
9  2.008432e+06 -18173144.0  1

In [24]:
# Construct the displacement dataframe from the raw simulator displacement output data.
# Get the size of each dimension in numpy array.
# m-> the number of time steps in the simulation.
# n-> the number of bodies in the simulation.
# r-> number of dimensions in the vector holding the acceleration, displacement, etc.
dis_m,dis_n,dis_r = stacked_raw_dis.shape
# Stack the XY or XYZ arrays of each body into columns, removing a dimension.
# np.column_stack() -> takes a sequence of 1D arrays and stacks them as columns in a 2D matrix.
# np.arange() provides evenly spaced values that repeat n times.  The new index.
# Had to add 1 to arange to go from 1 to 79 instead of 0.
dis_arr = np.column_stack(
    (np.repeat(np.arange(1, dis_m+1, 1),dis_n), 
     np.tile(np.arange(0,dis_n,1),dis_m), 
     stacked_raw_dis.reshape(dis_m*dis_n,-1))
)
# Create dataframe from stacked column array.
dis_df = pd.DataFrame(dis_arr)
# Delete intermediate numpy arrays and original data from memory.
del dis_arr
gc.collect()
# Use df.groupby() to group by time step or planent and create MultiIndex for easy data referencing.
dis_df = dis_df.groupby([0,1]).mean()
dis_df.index.names = ['time_step', 'body']
# Drop the time steps that could not be used for getting future data.
# Create list of time steps to drop.
beg_drop_index = max(dis_df.index.levels[0]) - num_ts_to_predict + 1
end_drop_index = max(dis_df.index.levels[0]) + 1
drop_list = list(range(int(beg_drop_index), int(end_drop_index)))
dis_df.drop(drop_list, level=0, inplace=True)
# Create list of columns 
cols = ['dis_x', 'dis_y']
for i in range(1, num_ts_to_predict+1):
    cols.append('dis_x_' + str(i))
    cols.append('dis_y_' + str(i))
dis_df.columns = cols
# Drop dis_x and dis_y columns since we won't need then for ML training input.
dis_df.drop(['dis_x', 'dis_y'], axis=1,inplace=True)
# View final velocity dataframe with future time steps.
idx = pd.IndexSlice
dis_df.loc[idx[0:2,:], :]

dis_x_1     dis_y_1      dis_x_2     dis_y_2      dis_x_3  \
time_step body                                                                  
1.0       0.0   2793426.250 -16287124.0  2632350.500 -16363946.0  2464677.750   
          1.0   4568526.000 -19268170.0  4438960.500 -19346324.0  4287897.500   
          2.0   3851763.750 -17673008.0  3701030.000 -17753962.0  3538769.000   
          3.0   1392847.500 -14406107.0  1226175.375 -14480070.0  1055592.875   
          4.0   3899068.500 -18968974.0  3756578.500 -19045012.0  3598410.250   
          5.0   2934459.750 -17635392.0  2778320.500 -17711628.0  2612979.500   
          6.0   2827053.750 -17423784.0  2669699.250 -17499962.0  2503739.750   
          7.0   3247631.250 -17700644.0  3093387.500 -17778078.0  2929107.000   
          8.0   2483720.750 -14158472.0  2317639.000 -14233828.0  2147703.750   
          9.0   3723638.500 -17510468.0  3571131.500 -17590806.0  3407936.500   
2.0       0.0   2632350.500 -16363946.0  2464677.750 -16435630.0  2293767.000   
          1.0   4438960.500 -19346324.0  4287897.500 -19418024.0  4127283.750   
          2.0   3701030.000 -17753962.0  3538769.000 -17827416.0  3371243.250   
          3.0   1226175.375 -14480070.0  1055592.875 -14550740.0   882842.375   
          4.0   3756578.500 -19045012.0  3598410.250 -19115828.0  3433186.000   
          5.0   2778320.500 -17711628.0  2612979.500 -17782862.0  2443287.000   
          6.0   2669699.250 -17499962.0  2503739.750 -17571200.0  2333675.000   
          7.0   3093387.500 -17778078.0  2929107.000 -17849858.0  2760146.250   
          8.0   2317639.000 -14233828.0  2147703.750 -14305032.0  1975713.750   
          9.0   3571131.500 -17590806.0  3407936.500 -17663988.0  3239826.000   

                   dis_y_3      dis_x_4     dis_y_4       dis_x_5     dis_y_5  \
time_step body                                                                  
1.0       0.0  -16435630.0  2293767.000 -16504681.0  2.120747e+06 -16571942.0   
          1.0  -19418024.0  4127283.750 -19486436.0  3.961300e+06 -19552570.0   
          2.0  -17827416.0  3371243.250 -17897198.0  3.200590e+06 -17964586.0   
          3.0  -14550740.0   882842.375 -14619644.0  7.084965e+05 -14687290.0   
          4.0  -19115828.0  3433186.000 -19183866.0  3.263874e+06 -19249912.0   
          5.0  -17782862.0  2443287.000 -17851472.0  2.270883e+06 -17918242.0   
          6.0  -17571200.0  2333675.000 -17639854.0  2.161025e+06 -17706700.0   
          7.0  -17849858.0  2760146.250 -17918730.0  2.588324e+06 -17985612.0   
          8.0  -14305032.0  1975713.750 -14374086.0  1.802266e+06 -14441657.0   
          9.0  -17663988.0  3239826.000 -17733650.0  3.068766e+06 -17800998.0   
2.0       0.0  -16504681.0  2120746.750 -16571942.0  1.946099e+06 -16637756.0   
          1.0  -19486436.0  3961300.000 -19552570.0  3.791803e+06 -19616860.0   
          2.0  -17897198.0  3200589.750 -17964586.0  3.027743e+06 -18030120.0   
          3.0  -14619644.0   708496.500 -14687290.0  5.327919e+05 -14753891.0   
          4.0  -19183866.0  3263874.500 -19249912.0  3.091777e+06 -19314308.0   
          5.0  -17851472.0  2270882.750 -17918242.0  2.096473e+06 -17983508.0   
          6.0  -17639854.0  2161024.750 -17706700.0  1.986442e+06 -17772068.0   
          7.0  -17918730.0  2588323.750 -17985612.0  2.414426e+06 -18050892.0   
          8.0  -14374086.0  1802266.125 -14441657.0  1.627608e+06 -14508027.0   
          9.0  -17733650.0  3068765.750 -17800998.0  2.895612e+06 -17866552.0   

                     dis_x_6     dis_y_6       dis_x_7     dis_y_7  \
time_step body                                                       
1.0       0.0   1.946099e+06 -16637756.0  1.770061e+06 -16702301.0   
          1.0   3.791803e+06 -19616860.0  3.619740e+06 -19679524.0   
          2.0   3.027743e+06 -18030120.0  2.853172e+06 -18094068.0   
          3.0   5.327919e+05 -14753891.0  3.558378e+05 -14819545.0   
          4.0   3.091777e+06 -1931

In [25]:
dis_df.shape

(399790, 40)

### Converting Mass to Pandas DataFrame

In [26]:
stacked_raw_mass = np.array(mass_list)
stacked_raw_mass

array([1476., 2824., 2360., 3703., 1801., 1521.,  614., 3559., 3512.,
       1805.], dtype=float32)

In [27]:
# Construct the mass dataframe from the raw simulator mass output data.
# Get the size of each dimension in numpy array.
# m-> the number of time steps in the simulation.
# n-> the number of bodies in the simulation.
# r-> number of dimensions in the vector holding the acceleration, displacement, etc.
mass_n = stacked_raw_mass.shape[0]
# Stack the Mass column with the indexing columns.  Mass column will be repeated by the number
# of time steps.
# np.column_stack() -> takes a sequence of 1D arrays and stacks them as columns in a 2D matrix.
# np.arange() provides evenly spaced values that repeat n times.  The new index.
# Using displacement dataframe dimensions to copy the masses enough.
mass_arr = np.column_stack(
     (np.repeat(np.arange(1, dis_m+1, 1),mass_n), 
     np.tile(np.arange(0,mass_n,1), dis_m),
     np.tile(stacked_raw_mass.reshape(mass_n,), dis_m))
)
# Create dataframe from stacked column array.
mass_df = pd.DataFrame(mass_arr)
# Delete intermediate numpy arrays and original data from memory.
del mass_arr
gc.collect()
# Use df.groupby() to group by time step or planent and create MultiIndex for easy data referencing.
mass_df = mass_df.groupby([0,1]).mean()
mass_df.index.names = ['time_step', 'body']
mass_df.columns = ['mass']
# Drop the time steps that could not be used for getting future data.
# Create list of time steps to drop.
beg_drop_index = max(mass_df.index.levels[0]) - num_ts_to_predict + 1
end_drop_index = max(mass_df.index.levels[0]) + 1
drop_list = list(range(int(beg_drop_index), int(end_drop_index)))
mass_df.drop(drop_list, axis=0, inplace=True)
mass_df.head(15)

mass
time_step body        
1.0       0.0   1476.0
          1.0   2824.0
          2.0   2360.0
          3.0   3703.0
          4.0   1801.0
          5.0   1521.0
          6.0    614.0
          7.0   3559.0
          8.0   3512.0
          9.0   1805.0
2.0       0.0   1476.0
          1.0   2824.0
          2.0   2360.0
          3.0   3703.0
          4.0   1801.0

In [28]:
mass_df.shape

(399790, 1)

# Merge the Mass, Acceleration, Velocity, and Displacement Data

In [29]:
# Copy mass dataframe to start creating merged version.  Delete mass df afterwards.
merged_data = mass_df.copy(deep=True)
merged_data = pd.merge(merged_data, acc_df, left_index=True, right_index=True, how='outer')
# Delete mass_df and acc_df
del mass_df
del acc_df
gc.collect()
merged_data.head(15)

mass     acc_x     acc_y
time_step body                            
1.0       0.0   1476.0 -0.003350 -0.003894
          1.0   2824.0  0.001788 -0.004374
          2.0   2360.0 -0.001583 -0.004751
          3.0   3703.0 -0.004363 -0.003255
          4.0   1801.0 -0.000145 -0.003863
          5.0   1521.0 -0.002421 -0.003808
          6.0    614.0 -0.002636 -0.003789
          7.0   3559.0 -0.002112 -0.004053
          8.0   3512.0 -0.004331 -0.003563
          9.0   1805.0 -0.001876 -0.004625
2.0       0.0   1476.0 -0.004979 -0.002624
          1.0   2824.0 -0.003496 -0.002706
          2.0   2360.0 -0.004488 -0.002831
          3.0   3703.0 -0.005246 -0.002474
          4.0   1801.0 -0.004093 -0.002597

In [30]:
# Merge in the velocity data.
merged_data = pd.merge(merged_data, vel_df, left_index=True, right_index=True, how='outer')
del vel_df
gc.collect()
merged_data.head(15)

mass     acc_x     acc_y        vel_x         vel_y  \
time_step body                                                          
1.0       0.0   1476.0 -0.003350 -0.003894  4071.568604 -22489.677734   
          1.0   2824.0  0.001788 -0.004374  6419.551758 -26621.166016   
          2.0   2360.0 -0.001583 -0.004751  5501.831055 -24396.433594   
          3.0   3703.0 -0.004363 -0.003255  2148.510742 -19890.517578   
          4.0   1801.0 -0.000145 -0.003863  5535.345703 -26215.746094   
          5.0   1521.0 -0.002421 -0.003808  4247.180664 -24364.169922   
          6.0    614.0 -0.002636 -0.003789  4102.775879 -24070.669922   
          7.0   3559.0 -0.002112 -0.004053  4675.142090 -24449.644531   
          8.0   3512.0 -0.004331 -0.003563  3662.585938 -19540.166016   
          9.0   1805.0 -0.001876 -0.004625  5330.547852 -24173.341797   
2.0       0.0   1476.0 -0.004979 -0.002624  3879.758545 -22621.005859   
          1.0   2824.0 -0.003496 -0.002706  6345.174805 -26761.347656   
          2.0   2360.0 -0.004488 -0.002831  5349.671875 -24545.843750   
          3.0   3703.0 -0.005246 -0.002474  1934.510498 -20008.482422   
          4.0   1801.0 -0.004093 -0.002597  5415.373047 -26345.796875   

                    vel_x_1       vel_y_1      vel_x_2       vel_y_2  \
time_step body                                                         
1.0       0.0   3879.758545 -22621.005859  3656.042480 -22727.703125   
          1.0   6345.174805 -26761.347656  6165.222656 -26869.894531   
          2.0   5349.671875 -24545.843750  5140.319336 -24658.281250   
          3.0   1934.510498 -20008.482422  1703.021362 -20111.208984   
          4.0   5415.373047 -26345.796875  5217.470215 -26451.404297   
          5.0   4075.638672 -24493.599609  3858.778564 -24599.482422   
          6.0   3926.463379 -24199.699219  3707.915527 -24305.501953   
          7.0   4510.599121 -24584.228516  4296.371582 -24691.775391   
          8.0   3449.612061 -19664.544922  3218.943115 -19769.205078   
          9.0   5171.720215 -24320.093750  4959.904785 -24431.673828   
2.0       0.0   3656.042480 -22727.703125  3423.163574 -22827.263672   
          1.0   6165.222656 -26869.894531  5955.413086 -26969.478516   
          2.0   5140.319336 -24658.281250  4914.957031 -24760.298828   
          3.0   1703.021362 -20111.208984  1466.101196 -20209.361328   
          4.0   5217.470215 -26451.404297  4997.791992 -26549.761719   

                    vel_x_3       vel_y_3      vel_x_4       vel_y_4  \
time_step body                                                         
1.0       0.0   3423.163574 -22827.263672  3185.787598 -22923.167969   
          1.0   5955.413086 -26969.478516  5732.338379 -27064.494141   
          2.0   4914.957031 -24760.298828  4682.282227 -24857.218750   
          3.0   1466.101196 -20209.361328  1226.169922 -20305.060547   
          4.0   4997.791992 -26549.761719  4768.313965 -26644.257812   
          5.0   3629.138184 -24698.419922  3393.454102 -24793.710938   
          6.0   3477.416260 -24404.443359  3241.215332 -24499.796875   
          7.0   4068.204102 -24791.468750  3833.536377 -24887.125000   
          8.0   2982.921875 -19868.099609  2744.046875 -19964.007812   
          9.0   4733.245117 -24533.316406  4499.758301 -24630.070312   
2.0       0.0   3185.787598 -22923.167969  2945.481445 -23016.585938   
          1.0   5732.338379 -27064.494141  5501.805664 -27156.347656   
          2.0   4682.282227 -24857.218750  4445.263672 -24950.814453   
          3.0   1226.169922 -20305.060547   984.022949 -20399.013672   
          4.0   4768.313965 -26644.257812  4533.159180 -26735.990234   

                    vel_x_5       vel_y_5      vel_x_6       vel_y_6  \
time_step body                                                         
1.0       0.0   2945.481445 -23016.585938  2702.914795 -23107.994141   
          1.0   5501.805664 -27156.347656  5266.393066 -27245.638672   
          2.0   4445.263672 -24950.814

In [31]:
# Merge in the displacement data
merged_data = pd.merge(merged_data, dis_df, left_index=True, right_index=True, how='outer')
del dis_df
gc.collect()
merged_data.head(15)

mass     acc_x     acc_y        vel_x         vel_y  \
time_step body                                                          
1.0       0.0   1476.0 -0.003350 -0.003894  4071.568604 -22489.677734   
          1.0   2824.0  0.001788 -0.004374  6419.551758 -26621.166016   
          2.0   2360.0 -0.001583 -0.004751  5501.831055 -24396.433594   
          3.0   3703.0 -0.004363 -0.003255  2148.510742 -19890.517578   
          4.0   1801.0 -0.000145 -0.003863  5535.345703 -26215.746094   
          5.0   1521.0 -0.002421 -0.003808  4247.180664 -24364.169922   
          6.0    614.0 -0.002636 -0.003789  4102.775879 -24070.669922   
          7.0   3559.0 -0.002112 -0.004053  4675.142090 -24449.644531   
          8.0   3512.0 -0.004331 -0.003563  3662.585938 -19540.166016   
          9.0   1805.0 -0.001876 -0.004625  5330.547852 -24173.341797   
2.0       0.0   1476.0 -0.004979 -0.002624  3879.758545 -22621.005859   
          1.0   2824.0 -0.003496 -0.002706  6345.174805 -26761.347656   
          2.0   2360.0 -0.004488 -0.002831  5349.671875 -24545.843750   
          3.0   3703.0 -0.005246 -0.002474  1934.510498 -20008.482422   
          4.0   1801.0 -0.004093 -0.002597  5415.373047 -26345.796875   

                    vel_x_1       vel_y_1      vel_x_2       vel_y_2  \
time_step body                                                         
1.0       0.0   3879.758545 -22621.005859  3656.042480 -22727.703125   
          1.0   6345.174805 -26761.347656  6165.222656 -26869.894531   
          2.0   5349.671875 -24545.843750  5140.319336 -24658.281250   
          3.0   1934.510498 -20008.482422  1703.021362 -20111.208984   
          4.0   5415.373047 -26345.796875  5217.470215 -26451.404297   
          5.0   4075.638672 -24493.599609  3858.778564 -24599.482422   
          6.0   3926.463379 -24199.699219  3707.915527 -24305.501953   
          7.0   4510.599121 -24584.228516  4296.371582 -24691.775391   
          8.0   3449.612061 -19664.544922  3218.943115 -19769.205078   
          9.0   5171.720215 -24320.093750  4959.904785 -24431.673828   
2.0       0.0   3656.042480 -22727.703125  3423.163574 -22827.263672   
          1.0   6165.222656 -26869.894531  5955.413086 -26969.478516   
          2.0   5140.319336 -24658.281250  4914.957031 -24760.298828   
          3.0   1703.021362 -20111.208984  1466.101196 -20209.361328   
          4.0   5217.470215 -26451.404297  4997.791992 -26549.761719   

                    vel_x_3       vel_y_3      vel_x_4       vel_y_4  \
time_step body                                                         
1.0       0.0   3423.163574 -22827.263672  3185.787598 -22923.167969   
          1.0   5955.413086 -26969.478516  5732.338379 -27064.494141   
          2.0   4914.957031 -24760.298828  4682.282227 -24857.218750   
          3.0   1466.101196 -20209.361328  1226.169922 -20305.060547   
          4.0   4997.791992 -26549.761719  4768.313965 -26644.257812   
          5.0   3629.138184 -24698.419922  3393.454102 -24793.710938   
          6.0   3477.416260 -24404.443359  3241.215332 -24499.796875   
          7.0   4068.204102 -24791.468750  3833.536377 -24887.125000   
          8.0   2982.921875 -19868.099609  2744.046875 -19964.007812   
          9.0   4733.245117 -24533.316406  4499.758301 -24630.070312   
2.0       0.0   3185.787598 -22923.167969  2945.481445 -23016.585938   
          1.0   5732.338379 -27064.494141  5501.805664 -27156.347656   
          2.0   4682.282227 -24857.218750  4445.263672 -24950.814453   
          3.0   1226.169922 -20305.060547   984.022949 -20399.013672   
          4.0   4768.313965 -26644.257812  4533.159180 -26735.990234   

                    vel_x_5       vel_y_5      vel_x_6       vel_y_6  \
time_step body                                                         
1.0       0.0   2945.481445 -23016.585938  2702.914795 -23107.994141   
          1.0   5501.805664 -27156.347656  5266.393066 -27245.638672   
          2.0   4445.263672 -24950.814

In [32]:
# Rearrange columns so they are in the needed order.
# Create list of what the column order should be.
cols = []
cols.extend(['mass', 'acc_x', 'acc_y', 'vel_x', 'vel_y'])
# Loop over all the time steps we wanted to predict and rearrange the columns
# accordingly
for i in range(1,num_ts_to_predict+1):
    cols.append('dis_x_' + str(i))
    cols.append('dis_y_' + str(i))
    cols.append('vel_x_' + str(i))
    cols.append('vel_y_' + str(i))
# Rearrange columns using the create columns list.
merged_data = merged_data[cols]
merged_data.head(15)

mass     acc_x     acc_y        vel_x         vel_y  \
time_step body                                                          
1.0       0.0   1476.0 -0.003350 -0.003894  4071.568604 -22489.677734   
          1.0   2824.0  0.001788 -0.004374  6419.551758 -26621.166016   
          2.0   2360.0 -0.001583 -0.004751  5501.831055 -24396.433594   
          3.0   3703.0 -0.004363 -0.003255  2148.510742 -19890.517578   
          4.0   1801.0 -0.000145 -0.003863  5535.345703 -26215.746094   
          5.0   1521.0 -0.002421 -0.003808  4247.180664 -24364.169922   
          6.0    614.0 -0.002636 -0.003789  4102.775879 -24070.669922   
          7.0   3559.0 -0.002112 -0.004053  4675.142090 -24449.644531   
          8.0   3512.0 -0.004331 -0.003563  3662.585938 -19540.166016   
          9.0   1805.0 -0.001876 -0.004625  5330.547852 -24173.341797   
2.0       0.0   1476.0 -0.004979 -0.002624  3879.758545 -22621.005859   
          1.0   2824.0 -0.003496 -0.002706  6345.174805 -26761.347656   
          2.0   2360.0 -0.004488 -0.002831  5349.671875 -24545.843750   
          3.0   3703.0 -0.005246 -0.002474  1934.510498 -20008.482422   
          4.0   1801.0 -0.004093 -0.002597  5415.373047 -26345.796875   

                    dis_x_1     dis_y_1      vel_x_1       vel_y_1  \
time_step body                                                       
1.0       0.0   2793426.250 -16287124.0  3879.758545 -22621.005859   
          1.0   4568526.000 -19268170.0  6345.174805 -26761.347656   
          2.0   3851763.750 -17673008.0  5349.671875 -24545.843750   
          3.0   1392847.500 -14406107.0  1934.510498 -20008.482422   
          4.0   3899068.500 -18968974.0  5415.373047 -26345.796875   
          5.0   2934459.750 -17635392.0  4075.638672 -24493.599609   
          6.0   2827053.750 -17423784.0  3926.463379 -24199.699219   
          7.0   3247631.250 -17700644.0  4510.599121 -24584.228516   
          8.0   2483720.750 -14158472.0  3449.612061 -19664.544922   
          9.0   3723638.500 -17510468.0  5171.720215 -24320.093750   
2.0       0.0   2632350.500 -16363946.0  3656.042480 -22727.703125   
          1.0   4438960.500 -19346324.0  6165.222656 -26869.894531   
          2.0   3701030.000 -17753962.0  5140.319336 -24658.281250   
          3.0   1226175.375 -14480070.0  1703.021362 -20111.208984   
          4.0   3756578.500 -19045012.0  5217.470215 -26451.404297   

                    dis_x_2     dis_y_2      vel_x_2       vel_y_2  \
time_step body                                                       
1.0       0.0   2632350.500 -16363946.0  3656.042480 -22727.703125   
          1.0   4438960.500 -19346324.0  6165.222656 -26869.894531   
          2.0   3701030.000 -17753962.0  5140.319336 -24658.281250   
          3.0   1226175.375 -14480070.0  1703.021362 -20111.208984   
          4.0   3756578.500 -19045012.0  5217.470215 -26451.404297   
          5.0   2778320.500 -17711628.0  3858.778564 -24599.482422   
          6.0   2669699.250 -17499962.0  3707.915527 -24305.501953   
          7.0   3093387.500 -17778078.0  4296.371582 -24691.775391   
          8.0   2317639.000 -14233828.0  3218.943115 -19769.205078   
          9.0   3571131.500 -17590806.0  4959.904785 -24431.673828   
2.0       0.0   2464677.750 -16435630.0  3423.163574 -22827.263672   
          1.0   4287897.500 -19418024.0  5955.413086 -26969.478516   
          2.0   3538769.000 -17827416.0  4914.957031 -24760.298828   
          3.0   1055592.875 -14550740.0  1466.101196 -20209.361328   
          4.0   3598410.250 -19115828.0  4997.791992 -26549.761719   

                    dis_x_3     dis_y_3      vel_x_3       vel_y_3  \
time_step body                                                       
1.0       0.0   2464677.750 -16435630.0  3423.163574 -22827.263672   
          1.0   4287897.500 -19418024.0  5955.413086 -26969.478516   
          2.0   3538769.000 -17827416.0  4914.957031 -24760.298828   
          3.0   1055592.875 -14550740.0  146

# Create Body Time Series Data Format

In [33]:
merged_data_time_series = merged_data.copy(deep=True)
merged_data_time_series = merged_data_time_series.swaplevel('time_step', 'body').sort_index(level=0)
merged_data_time_series.head(15)

mass     acc_x     acc_y        vel_x         vel_y  \
body time_step                                                          
0.0  1.0        1476.0 -0.003350 -0.003894  4071.568604 -22489.677734   
     2.0        1476.0 -0.004979 -0.002624  3879.758545 -22621.005859   
     3.0        1476.0 -0.005313 -0.002366  3656.042480 -22727.703125   
     4.0        1476.0 -0.005451 -0.002256  3423.163574 -22827.263672   
     5.0        1476.0 -0.005532 -0.002189  3185.787598 -22923.167969   
     6.0        1476.0 -0.005590 -0.002138  2945.481445 -23016.585938   
     7.0        1476.0 -0.005638 -0.002095  2702.914795 -23107.994141   
     8.0        1476.0 -0.005680 -0.002056  2458.417725 -23197.640625   
     9.0        1476.0 -0.005719 -0.002019  2212.165527 -23285.652344   
     10.0       1476.0 -0.005757 -0.001984  1964.258301 -23372.097656   
     11.0       1476.0 -0.005793 -0.001949  1714.756470 -23457.017578   
     12.0       1476.0 -0.005829 -0.001914  1463.693481 -23540.435547   
     13.0       1476.0 -0.005865 -0.001879  1211.088501 -23622.357422   
     14.0       1476.0 -0.005900 -0.001845   956.949890 -23702.792969   
     15.0       1476.0 -0.005936 -0.001810   701.279907 -23781.734375   

                     dis_x_1     dis_y_1      vel_x_1       vel_y_1  \
body time_step                                                        
0.0  1.0        2.793426e+06 -16287124.0  3879.758545 -22621.005859   
     2.0        2.632350e+06 -16363946.0  3656.042480 -22727.703125   
     3.0        2.464678e+06 -16435630.0  3423.163574 -22827.263672   
     4.0        2.293767e+06 -16504681.0  3185.787598 -22923.167969   
     5.0        2.120747e+06 -16571942.0  2945.481445 -23016.585938   
     6.0        1.946099e+06 -16637756.0  2702.914795 -23107.994141   
     7.0        1.770061e+06 -16702301.0  2458.417725 -23197.640625   
     8.0        1.592759e+06 -16765670.0  2212.165527 -23285.652344   
     9.0        1.414266e+06 -16827910.0  1964.258301 -23372.097656   
     10.0       1.234625e+06 -16889052.0  1714.756470 -23457.017578   
     11.0       1.053859e+06 -16949114.0  1463.693481 -23540.435547   
     12.0       8.719838e+05 -17008098.0  1211.088501 -23622.357422   
     13.0       6.890039e+05 -17066010.0   956.949890 -23702.792969   
     14.0       5.049215e+05 -17122848.0   701.279907 -23781.734375   
     15.0       3.197347e+05 -17178610.0   444.075989 -23859.179688   

                     dis_x_2     dis_y_2      vel_x_2       vel_y_2  \
body time_step                                                        
0.0  1.0        2.632350e+06 -16363946.0  3656.042480 -22727.703125   
     2.0        2.464678e+06 -16435630.0  3423.163574 -22827.263672   
     3.0        2.293767e+06 -16504681.0  3185.787598 -22923.167969   
     4.0        2.120747e+06 -16571942.0  2945.481445 -23016.585938   
     5.0        1.946099e+06 -16637756.0  2702.914795 -23107.994141   
     6.0        1.770061e+06 -16702301.0  2458.417725 -23197.640625   
     7.0        1.592759e+06 -16765670.0  2212.165527 -23285.652344   
     8.0        1.414266e+06 -16827910.0  1964.258301 -23372.097656   
     9.0        1.234625e+06 -16889052.0  1714.756470 -23457.017578   
     10.0       1.053859e+06 -16949114.0  1463.693481 -23540.435547   
     11.0       8.719838e+05 -17008098.0  1211.088501 -23622.357422   
     12.0       6.890039e+05 -17066010.0   956.949890 -23702.792969   
     13.0       5.049215e+05 -17122848.0   701.279907 -23781.734375   
     14.0       3.197347e+05 -17178610.0   444.075989 -23859.179688   
     15.0       1.334387e+05 -17233282.0   185.331543 -23935.115234   

                     dis_x_3     dis_y_3      vel_x_3       vel_y_3  \
body time_step                                                        
0.0  1.0        2.464678e+06 -16435630.0  3423.163574 -22827.263672   
     2.0        2.293767e+06 -16504681.0  3185.787598 -22923.167969   
     3.0        2.120747e+06 -16571942.0  2945.481445 -23016.585938   
     

# Attempt Converting Merged Datasets to Numpy Arrays and Save as Both Pd dataframes and Np Arrays

In [34]:
merged_data.to_numpy().shape

(399790, 85)

In [35]:
dim0 = len(merged_data.index.get_level_values(0).unique())
dim1 = len(merged_data.index.get_level_values(1).unique())
dim2 = merged_data.shape[1]
merged_data_ndarray = merged_data.to_numpy().reshape((dim0, dim1, dim2))
merged_data_ndarray[0,0]

array([ 1.47600000e+03, -3.34952190e-03, -3.89396958e-03,  4.07156860e+03,
       -2.24896777e+04,  2.79342625e+06, -1.62871240e+07,  3.87975854e+03,
       -2.26210059e+04,  2.63235050e+06, -1.63639460e+07,  3.65604248e+03,
       -2.27277031e+04,  2.46467775e+06, -1.64356300e+07,  3.42316357e+03,
       -2.28272637e+04,  2.29376700e+06, -1.65046810e+07,  3.18578760e+03,
       -2.29231680e+04,  2.12074675e+06, -1.65719420e+07,  2.94548145e+03,
       -2.30165859e+04,  1.94609862e+06, -1.66377560e+07,  2.70291479e+03,
       -2.31079941e+04,  1.77006075e+06, -1.67023010e+07,  2.45841772e+03,
       -2.31976406e+04,  1.59275912e+06, -1.67656700e+07,  2.21216553e+03,
       -2.32856523e+04,  1.41426600e+06, -1.68279100e+07,  1.96425830e+03,
       -2.33720977e+04,  1.23462462e+06, -1.68890520e+07,  1.71475647e+03,
       -2.34570176e+04,  1.05385925e+06, -1.69491140e+07,  1.46369348e+03,
       -2.35404355e+04,  8.71983750e+05, -1.70080980e+07,  1.21108850e+03,
       -2.36223574e+04,  

In [36]:
dim0 = len(merged_data_time_series.index.get_level_values(0).unique())
dim1 = len(merged_data_time_series.index.get_level_values(1).unique())
dim2 = merged_data.shape[1]
merged_data_time_series_ndarray = merged_data_time_series.to_numpy().reshape((dim0, dim1, dim2))
merged_data_time_series_ndarray[0,5]

array([ 1.47600000e+03, -5.59008354e-03, -2.13832036e-03,  2.94548145e+03,
       -2.30165859e+04,  1.94609862e+06, -1.66377560e+07,  2.70291479e+03,
       -2.31079941e+04,  1.77006075e+06, -1.67023010e+07,  2.45841772e+03,
       -2.31976406e+04,  1.59275912e+06, -1.67656700e+07,  2.21216553e+03,
       -2.32856523e+04,  1.41426600e+06, -1.68279100e+07,  1.96425830e+03,
       -2.33720977e+04,  1.23462462e+06, -1.68890520e+07,  1.71475647e+03,
       -2.34570176e+04,  1.05385925e+06, -1.69491140e+07,  1.46369348e+03,
       -2.35404355e+04,  8.71983750e+05, -1.70080980e+07,  1.21108850e+03,
       -2.36223574e+04,  6.89003938e+05, -1.70660100e+07,  9.56949890e+02,
       -2.37027930e+04,  5.04921531e+05, -1.71228480e+07,  7.01279907e+02,
       -2.37817344e+04,  3.19734719e+05, -1.71786100e+07,  4.44075989e+02,
       -2.38591797e+04,  1.33438719e+05, -1.72332820e+07,  1.85331543e+02,
       -2.39351152e+04, -5.39725508e+04, -1.72868620e+07, -7.49618759e+01,
       -2.40095312e+04, -

## Save the Numpy Arrays and Pandas Dataframes

In [37]:
# Set the output directory.
out_dir = 'output/'

Save the dataframes by pickling them.

In [38]:
# Save using 'default' as the key.
# https://pythontic.com/pandas/serialization/hdf5

#merged_data.to_hdf(out_dir + 'sim_data_df-ts-body.hdf5', 'default')

file_name = '3-hour_10-sats_predict-20-steps_720ts_1200000steps_30freq.hdf5'
merged_data_time_series.to_hdf(out_dir + file_name, 'default')

# merged_data.to_pickle(out_dir + 'sim_data_df-ts-body.pkl')
# merged_data_time_series.to_pickle(out_dir + 'sim_data_df-body-ts.pkl')

Save the dataframes to XLSX files to view in Excel. \
Some larger datasets can't be saved to Excel.  Takes forever to parse the file.

In [ ]:
# merged_data.to_excel(out_dir + 'sim_data_df-ts-body.xlsx')
# merged_data_time_series.to_excel(out_dir + 'sim_data_df-body-ts.xlsx')

Save the numpy arrays by using numpy's saving function.

In [ ]:
#np.save(out_dir + 'sim_data_np-ts-body.npy', merged_data_ndarray)
#np.save(out_dir + 'sim_data_np-body-ts.npy', merged_data_time_series_ndarray)